# Hugging Face Spaces From A Notebook

> A demo of using nbdev with Hugging Face Spaces

## 1. Create a Gradio-enabled Space on Hugging Face

The first step is to create a space and select the appropriate sdk (which is Gradio in this example), per [these instructions](https://huggingface.co/docs/hub/spaces-overview#creating-a-new-space):

![](./create_space.png)

After you are done creating the space, **clone the repo per the instructions provided in the app.**  In this example, I ran the command `git clone https://huggingface.co/spaces/hamel/hfspace_demo`.

## 2. Make an app with Gradio

Below, we will create a [gradio](https://gradio.app/) app in a notebook and show you how to deploy it to [Hugging Face Spaces](https://huggingface.co/docs/hub/spaces).

First, lets specify the libraries we need, which in this case are `gradio` and `fastcore`:

In [ ]:
#|export
import gradio as gr
from fastcore.net import urljson, HTTPError

In [ ]:
#|export
def size(repo:str):
    "Returns the size in GB of a HuggingFace Dataset."
    url = f'https://huggingface.co/api/datasets/{repo}'
    try: resp = urljson(f'{url}/treesize/main')
    except HTTPError: return f'Did not find repo: {url}'
    gb = resp['size'] / 1e9
    return f'{gb:.2f} GB'

`size` take as an input a [Hugging Face Dataset](https://huggingface.co/docs/datasets/index) repo and returns the total size in GB of the data.

For example, we can check the size of [tglcourse/CelebA-faces-cropped-128](https://huggingface.co/datasets/tglcourse/CelebA-faces-cropped-128) like so:

In [ ]:
size("tglcourse/CelebA-faces-cropped-128")

'5.49 GB'

You can construct a simple UI with the `gradio.interface` and then call the `launch` method of that interface to display a preview in a notebook.  This is a great way to test your app to see if it works

In [ ]:
#|export
iface = gr.Interface(fn=size, inputs=gr.Text(value="tglcourse/CelebA-faces-cropped-128"), outputs="text")
iface.launch(width=500)

Running on local URL:  http://127.0.0.1:7860

To create a public link, set `share=True` in `launch()`.


(<gradio.routes.App>, 'http://127.0.0.1:7860/', None)

Note how running the `launch()` method in a notebook runs a webserver in the background.  Below, we call the `close()` method to close the webserver.

In [ ]:
# this is only necessary in a notebook
iface.close()

Closing server running on port: 7860


## 3. Converting This Notebook Into A Gradio App

In order to host this code on Hugging Faces spaces, you will export parts of this notebook to a script named `app.py`.  That is what the special `#|export` comment that you have seen in cells above do!  You can export code from this notebook like so:

In [ ]:
from nbdev.export import nb_export
nb_export('app.ipynb', lib_path='.', name='app')

<div>
<link rel="stylesheet" href="https://gradio.s3-us-west-2.amazonaws.com/2.6.5/static/bundle.css">
<div id="target"></div>
<script src="https://gradio.s3-us-west-2.amazonaws.com/2.6.5/static/bundle.js"></script>
<script>
launchGradioFromSpaces("abidlabs/question-answering", "#target")
</script>
</div>

### Understanding what is generated

Notice how the contents of app.py only contains the exported cells from this notebook:

In [ ]:
%pycat app.py

# AUTOGENERATED! DO NOT EDIT! File to edit: app.ipynb.

# %% auto 0
__all__ = ['iface', 'size']

# %% app.ipynb 6
import gradio as gr
from fastcore.net import urljson, HTTPError

# %% app.ipynb 7
def size(repo:str):
    "Returns the size in GB of a HuggingFace Dataset."
    url = f'https://huggingface.co/api/datasets/{repo}'
    try: resp = urljson(f'{url}/treesize/main')
    except HTTPError: return f'Did not find repo: {url}'
    gb = resp['size'] / 1e9
    return f'{gb:.2f} GB'

# %% app.ipynb 11
iface = gr.Interface(fn=size, inputs=gr.Text(value="tglcourse/CelebA-faces-cropped-128"), outputs="text")
iface.launch(width=500)


### Fill out `requirements.txt`

You must supply a requirements.txt file so the gradio app knows how to build your dependencies.  In this example, the only depdency other than gradio is `fastcore`.  You don't need to specify gradio itself as a depdendency in `requirements.txt` so our `requirements.txt` file has only one dependency:

In [ ]:
!cat requirements.txt

fastcore

## 4. Launch Your Gradio App

To launch your gradio app, you need to commit the changes in the Hugging Face repo:

```
git add -A; git commit -m "Add application files"; git push
```

## 5. Voilà!  Enjoy your Gradio App

After a couple of minutes, you will see your app published!  This app is published at https://huggingface.co/spaces/hamel/hfspace_demo.